**PLAN:**
1. Model szeregu czasowego sprawdzający wartości parametrów za 6 minut;
2. Sprawdzenie kombinacji;
3. Wybranie kombinacji, która da nam wartości najbliższe celu za 6 minut

In [1]:
import os
import numpy as np
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
import matplotlib.pyplot as plt
import seaborn as sns
from plotly.subplots import make_subplots

from itertools import product, combinations
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_squared_error

In [22]:
arrays = [np.linspace(-800, 801, 100), np.linspace(-0.0013, 0.0013, 100), np.linspace(-20, 20, 100)]

In [23]:
DELTAS_PROD = list(product(*arrays))

In [24]:
MEAN_REACTION_TIME = 30

In [25]:
ZMIENNE_MANIPULOWANE = ["001FCx00285_SPPV.PV",
                        "001XXXCALC01.NUM.PV[3]",
                        "001SCx00274_SPPV.PV",                  
                        "001FCx00241_sppv.pv"]
ZMIENNE_PIERSCIENIE = ["001NIR0SZRG.daca.pv",
                        "001NIR0S600.daca.pv",
                        "001NIR0S500.daca.pv",
                        "001NIR0S300.daca.pv",
                        "001NIR0S100.daca.pv"]

ZMIENNA_CELU = "001NIR0SZR0.daca.pv"
ZMIENNA_CZASU = 'Czas'

In [26]:
df = pd.read_csv('processed_data_zad2.csv')
# df = df.drop(labels=ZMIENNE_PIERSCIENIE, axis=1)

In [27]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3954000 entries, 0 to 3953999
Data columns (total 27 columns):
 #   Column                  Dtype  
---  ------                  -----  
 0   Czas                    object 
 1   001FCx00285_SPPV.PV     float64
 2   001XXXCALC01.NUM.PV[3]  float64
 3   001SCx00274_SPPV.PV     float64
 4   001FCx00241_sppv.pv     float64
 5   001NIR0SZR0.daca.pv     float64
 6   001NIR0SZRG.daca.pv     float64
 7   001NIR0S600.daca.pv     float64
 8   001NIR0S500.daca.pv     float64
 9   001NIR0S300.daca.pv     float64
 10  001NIR0S100.daca.pv     float64
 11  001FYx00206_SPSUM.pv    float64
 12  001FCx00231_SPPV.PV     float64
 13  001FCx00251_SPPV.PV     float64
 14  001FCx00281.PV          float64
 15  001FCx00262.PV          float64
 16  001FCx00261.PV          float64
 17  001XXXCALC01.NUM.PV[2]  float64
 18  prob_corg               float64
 19  prob_s                  float64
 20  sita_nadziarno          float64
 21  sita_podziarno          float64

In [28]:
def plot_date_range(df, start_date, stop_date):
    df = df.reset_index(drop=False)
    df = df[(df[ZMIENNA_CZASU]>=start_date) & (df[ZMIENNA_CZASU]<=stop_date)]
    fig = make_subplots(specs=[[{"secondary_y": True}]])
    fig.add_trace(go.Scatter(mode='lines',
                            x=df[ZMIENNA_CZASU],
                            y=df[ZMIENNA_CELU],
                            text='Straty KSR',
                            name='Straty KSR'))    
    fig.add_trace(go.Scatter(mode='lines',
                            x=df[ZMIENNA_CZASU],
                            y=df['001FCx00285_SPPV.PV'],                            
                            text='Przepływ powietrza dystrybucyjnego',
                            name='Przepływ powietrza dystrybucyjnego'),
                 secondary_y=True)
    
    return fig

In [29]:
def preprocess_df(df, start_date, stop_date):
    df[ZMIENNA_CZASU] = pd.to_datetime(df[ZMIENNA_CZASU])
    df = df[(df[ZMIENNA_CZASU]>=start_date) & (df[ZMIENNA_CZASU]<stop_date)]
    df = df.set_index(ZMIENNA_CZASU)
    df = df.resample('10S').mean()
    df = df.dropna().reset_index()
    df = df.set_index([ZMIENNA_CZASU, ZMIENNA_CELU])
    return df

In [30]:
df_april_train, df_april_test = preprocess_df(df, '2021-04-01', '2021-04-26'), preprocess_df(df, '2021-04-26', '2021-04-29')

In [31]:
df_april_train

001FCx00285_SPPV.PV  \
Czas                001NIR0SZR0.daca.pv                        
2021-04-19 00:00:00 23.320475                         2700.0   
2021-04-19 00:00:10 23.368764                         2700.0   
2021-04-19 00:00:20 23.397422                         2700.0   
2021-04-19 00:00:30 23.414602                         2700.0   
2021-04-19 00:00:40 23.456724                         2700.0   
...                                                      ...   
2021-04-25 23:59:10 24.206277                         2700.0   
2021-04-25 23:59:20 24.192292                         2700.0   
2021-04-25 23:59:30 24.141316                         2900.0   
2021-04-25 23:59:40 24.111355                         3500.0   
2021-04-25 23:59:50 24.074378                         3500.0   

                                         001XXXCALC01.NUM.PV[3]  \
Czas                001NIR0SZR0.daca.pv                           
2021-04-19 00:00:00 23.320475                              81.0   
2021-04-19 00:00:10 23.368764                              81.0   
2021-04-19 00:00:20 23.397422                              81.0   
2021-04-19 00:00:30 23.414602                              81.0   
2021-04-19 00:00:40 23.456724                              81.0   
...                                                         ...   
2021-04-25 23:59:10 24.206277                              80.0   
2021-04-25 23:59:20 24.192292                              80.0   
2021-04-25 23:59:30 24.141316                              80.0   
2021-04-25 23:59:40 24.111355                              80.0   
2021-04-25 23:59:50 24.074378                              80.0   

                                         001SCx00274_SPPV.PV  \
Czas                001NIR0SZR0.daca.pv                        
2021-04-19 00:00:00 23.320475                           50.0   
2021-04-19 00:00:10 23.368764                           50.0   
2021-04-19 00:00:20 23.397422                           50.0   
2021-04-19 00:00:30 23.414602                           50.0   
2021-04-19 00:00:40 23.456724                           50.0   
...                                                      ...   
2021-04-25 23:59:10 24.206277                           50.0   
2021-04-25 23:59:20 24.192292                           50.0   
2021-04-25 23:59:30 24.141316                           50.0   
2021-04-25 23:59:40 24.111355                           50.0   
2021-04-25 23:59:50 24.074378                           50.0   

                                         001FCx00241_sppv.pv  \
Czas                001NIR0SZR0.daca.pv                        
2021-04-19 00:00:00 23.320475                           31.0   
2021-04-19 00:00:10 23.368764                           31.0   
2021-04-19 00:00:20 23.397422                           31.0   
2021-04-19 00:00:30 23.414602                           31.0   
2021-04-19 00:00:40 23.456724                           31.0   
...                                                      ...   
2021-04-25 23:59:10 24.206277                           23.0   
2021-04-25 23:59:20 24.192292                           23.0   
2021-04-25 23:59:30 24.141316                           23.0   
2021-04-25 23:59:40 24.111355                           23.0   
2021-04-25 23:59:50 24.074378                           23.0   

                                         001NIR0SZRG.daca.pv  \
Czas                001NIR0SZR0.daca.pv                        
2021-04-19 00:00:00 23.320475                       0.870842   
2021-04-19 00:00:10 23.368764                       0.870579   
2021-04-19 00:00:20 23.397422                       0.870315   
2021-04-19 00:00:30 23.414602                       0.870052   
2021-04-19 00:00:40 23.456724                       0.869789   
...                                                      ...   
2021-04-25 23:59:10 24.206277                       0.867885   
2021-04-25 23:59:20 24.192292                       0.867448   
2021-04-25 23:59:30 24.141316 

In [32]:
df_april_lagged = df_april_train.shift(MEAN_REACTION_TIME).dropna().reset_index().set_index(ZMIENNA_CZASU)
df_test_lagged = df_april_test.shift(MEAN_REACTION_TIME).dropna().reset_index().set_index(ZMIENNA_CZASU)

In [33]:
df_april_lagged

001NIR0SZR0.daca.pv  001FCx00285_SPPV.PV  \
Czas                                                            
2021-04-19 00:05:00            23.442731               2700.0   
2021-04-19 00:05:10            23.417879               2700.0   
2021-04-19 00:05:20            23.399783               2700.0   
2021-04-19 00:05:30            23.392498               2700.0   
2021-04-19 00:05:40            23.395817               2700.0   
...                                  ...                  ...   
2021-04-25 23:59:10            24.206277               2000.0   
2021-04-25 23:59:20            24.192292               2000.0   
2021-04-25 23:59:30            24.141316               2000.0   
2021-04-25 23:59:40            24.111355               2000.0   
2021-04-25 23:59:50            24.074378               2000.0   

                     001XXXCALC01.NUM.PV[3]  001SCx00274_SPPV.PV  \
Czas                                                               
2021-04-19 00:05:00                    81.0                 50.0   
2021-04-19 00:05:10                    81.0                 50.0   
2021-04-19 00:05:20                    81.0                 50.0   
2021-04-19 00:05:30                    81.0                 50.0   
2021-04-19 00:05:40                    81.0                 50.0   
...                                     ...                  ...   
2021-04-25 23:59:10                    80.0                 55.0   
2021-04-25 23:59:20                    80.0                 55.0   
2021-04-25 23:59:30                    80.0                 55.0   
2021-04-25 23:59:40                    80.0                 55.0   
2021-04-25 23:59:50                    80.0                 55.0   

                     001FCx00241_sppv.pv  001NIR0SZRG.daca.pv  \
Czas                                                            
2021-04-19 00:05:00                 31.0             0.870842   
2021-04-19 00:05:10                 31.0             0.870579   
2021-04-19 00:05:20                 31.0             0.870315   
2021-04-19 00:05:30                 31.0             0.870052   
2021-04-19 00:05:40                 31.0             0.869789   
...                                  ...                  ...   
2021-04-25 23:59:10                 23.0             0.864561   
2021-04-25 23:59:20                 23.0             0.864844   
2021-04-25 23:59:30                 23.0             0.865128   
2021-04-25 23:59:40                 23.0             0.865412   
2021-04-25 23:59:50                 23.0             0.865740   

                     001NIR0S600.daca.pv  001NIR0S500.daca.pv  \
Czas                                                            
2021-04-19 00:05:00             1.513727             7.211709   
2021-04-19 00:05:10             1.513468             7.223036   
2021-04-19 00:05:20             1.513208             7.233054   
2021-04-19 00:05:30             1.512949             7.239280   
2021-04-19 00:05:40             1.512690             7.245265   
...                                  ...                  ...   
2021-04-25 23:59:10             1.583222             8.076830   
2021-04-25 23:59:20             1.583911             8.065430   
2021-04-25 23:59:30             1.584601             8.052659   
2021-04-25 23:59:40             1.585290             8.039028   
2021-04-25 23:59:50             1.585980             8.016300   

                     001NIR0S300.daca.pv  001NIR0S100.daca.pv  ...  \
Czas                                                           ...   
2021-04-19 00:05:00             7.297815             6.446786  ...   
2021-04-19 00:05:10             7.312535             6.448606  ...   
2021-04-19 00:05:20             7.327014             6.450426  ...   
2021-04-19 00:05:30             7.335812             6.452246  ...   
2021-04-19 00:05:40             7.342650             6.454066  ...   
...                                  ...                  ...  ...   
2021-04-25 23:59:10             7.8047

In [34]:
X_train, Y_train = df_april_lagged.drop(labels=ZMIENNA_CELU, axis=1), df_april_lagged[ZMIENNA_CELU]
X_test, Y_test = df_test_lagged.drop(labels=ZMIENNA_CELU, axis=1), df_test_lagged[ZMIENNA_CELU]

In [35]:
X_test

001FCx00285_SPPV.PV  001XXXCALC01.NUM.PV[3]  \
Czas                                                               
2021-04-26 00:05:00               3500.0                    80.0   
2021-04-26 00:05:10               3500.0                    80.0   
2021-04-26 00:05:20               3500.0                    80.0   
2021-04-26 00:05:30               3500.0                    80.0   
2021-04-26 00:05:40               3500.0                    80.0   
...                                  ...                     ...   
2021-04-28 23:59:10               2800.0                    80.0   
2021-04-28 23:59:20               2800.0                    80.0   
2021-04-28 23:59:30               2800.0                    80.0   
2021-04-28 23:59:40               2800.0                    80.0   
2021-04-28 23:59:50               2800.0                    80.0   

                     001SCx00274_SPPV.PV  001FCx00241_sppv.pv  \
Czas                                                            
2021-04-26 00:05:00                 50.0                 23.0   
2021-04-26 00:05:10                 50.0                 23.0   
2021-04-26 00:05:20                 50.0                 23.0   
2021-04-26 00:05:30                 50.0                 23.0   
2021-04-26 00:05:40                 50.0                 23.0   
...                                  ...                  ...   
2021-04-28 23:59:10                 42.0                 25.0   
2021-04-28 23:59:20                 42.0                 25.0   
2021-04-28 23:59:30                 42.0                 25.0   
2021-04-28 23:59:40                 42.0                 25.0   
2021-04-28 23:59:50                 42.0                 25.0   

                     001NIR0SZRG.daca.pv  001NIR0S600.daca.pv  \
Czas                                                            
2021-04-26 00:05:00             0.865698             1.582622   
2021-04-26 00:05:10             0.865260             1.581116   
2021-04-26 00:05:20             0.864823             1.579609   
2021-04-26 00:05:30             0.864326             1.578103   
2021-04-26 00:05:40             0.863948             1.576596   
...                                  ...                  ...   
2021-04-28 23:59:10             0.857175             1.566068   
2021-04-28 23:59:20             0.857283             1.564958   
2021-04-28 23:59:30             0.857376             1.563848   
2021-04-28 23:59:40             0.856985             1.562738   
2021-04-28 23:59:50             0.856324             1.561628   

                     001NIR0S500.daca.pv  001NIR0S300.daca.pv  \
Czas                                                            
2021-04-26 00:05:00             7.361827             7.547441   
2021-04-26 00:05:10             7.339526             7.537525   
2021-04-26 00:05:20             7.317166             7.527610   
2021-04-26 00:05:30             7.288108             7.517694   
2021-04-26 00:05:40             7.261646             7.507486   
...                                  ...                  ...   
2021-04-28 23:59:10             7.872827             8.150348   
2021-04-28 23:59:20             7.853224             8.124750   
2021-04-28 23:59:30             7.833620             8.101771   
2021-04-28 23:59:40             7.814017             8.111383   
2021-04-28 23:59:50             7.794414             8.090085   

                     001NIR0S100.daca.pv  001FYx00206_SPSUM.pv  ...  \
Czas                                                            ...   
2021-04-26 00:05:00             6.659287                 110.0  ...   
2021-04-26 00:05:10             6.657062                 110.0  ...   
2021-04-26 00:05:20             6.654836                 110.0  ...   
2021-04-26 00:05:30             6.652411                 110.0  ...   
2021-04-26 00:05:40             6.649166                 110.0  ...   
...                                  ...                   ...  ...   
2021-04-28 23:59:10           

In [36]:
model = LinearRegression()
model.fit(X_train, Y_train)
Y_pred = model.predict(X_test)

In [37]:
mean_squared_error(Y_pred, Y_test)

0.42915047856260274

In [38]:
keys_ = list(df_april_train.columns)
values = model.coef_
fi = pd.Series(dict(zip(keys_, values)))

In [39]:
px.bar(fi.sort_values(), orientation='h')

In [40]:
fig = go.Figure()
fig.add_trace(go.Scatter(mode='lines',
                        x=pd.to_datetime(Y_test.index.values),
                        y=Y_test,
                        text='Rzeczywiste wartości straty',
                        name='Rzeczywiste wartości straty'))    
fig.add_trace(go.Scatter(mode='lines',
                        x=pd.to_datetime(Y_test.index.values),
                        y=Y_pred,                            
                        text='Przewidywane wartości straty',
                        name='Przewidywane wartości straty'))

In [21]:
fig.write_image(os.path.join('images','baseline_model.png'))
fig.write_html(os.path.join('images','baseline_model.html'))